In [1]:
import re
import string

!pip install -U nltk

import nltk
nltk.download('punkt')
nltk.download('stopwords')
from nltk.tokenize import sent_tokenize # Sentence Tokenizer
from nltk.tokenize import word_tokenize # Word Tokenizer
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.probability import FreqDist

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

  Running setup.py install for nltk: started
    Running setup.py install for nltk: finished with status 'done'


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\jhump\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\jhump\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\stopwords.zip.


# 1) (optional) Scrape 100 Job Listings that contain the title "Data Scientist" from indeed.com

At a minimum your final dataframe of job listings should contain
- Job Title
- Job Description

In [6]:
# Imports for scraper

import requests
import time
from bs4 import BeautifulSoup

In [5]:
# Function below credit to EB/LSDS01


def query_generator(keyword, location, radius=50):

    '''A function that takes a search keyword (or keywords) and a city and returns the resulting query url'''

    if ' ' in keyword:
        keyword.replace(' ', '+')
    
    
    string1 = f"https://www.indeed.com/jobs?as_and={keyword}&as_phr=&as_any=&as_not=&as_ttl=&as_cmp=&jt=all&st=&"
    string2 = f"sr=directhire&as_src=&salary=&radius=50&l={location}&fromage=15&limit=10&sort=&psf=advsrch"
    query = string1+string2

    return query


test_query = query_generator("healthcare+scikit", "any")
print(test_query)

https://www.indeed.com/jobs?as_and=healthcare+scikit&as_phr=&as_any=&as_not=&as_ttl=&as_cmp=&jt=all&st=&sr=directhire&as_src=&salary=&radius=50&l=any&fromage=15&limit=10&sort=&psf=advsrch


## 2) Use NLTK to tokenize / clean the listings 

In [28]:
job_listings = pd.read_csv('job_listings.csv')

In [29]:
job_listings = job_listings.drop(columns='Unnamed: 0')
job_listings.head()

description  \
0  b"<div><div>Job Requirements:</div><ul><li><p>...   
1  b'<div>Job Description<br/>\n<br/>\n<p>As a Da...   
2  b'<div><p>As a Data Scientist you will be work...   
3  b'<div class="jobsearch-JobMetadataHeader icl-...   
4  b'<ul><li>Location: USA \xe2\x80\x93 multiple ...   

                          title  
0               Data scientist   
1              Data Scientist I  
2  Data Scientist - Entry Level  
3                Data Scientist  
4                Data Scientist

In [44]:
# Try reading in csv file using a context manager and decoding

with open('job_listings.csv', 'r', encoding='utf-8') as csvfile:
    job_listings = csvfile.read()

In [45]:
job_listings

',description,title\n0,"b""<div><div>Job Requirements:</div><ul><li><p>\\nConceptual understanding in Machine Learning models like Nai\\xc2\\xa8ve Bayes, K-Means, SVM, Apriori, Linear/ Logistic Regression, Neural, Random Forests, Decision Trees, K-NN along with hands-on experience in at least 2 of them</p>\\n</li><li><p>Intermediate to expert level coding skills in Python/R. (Ability to write functions, clean and efficient data manipulation are mandatory for this role)</p>\\n</li><li><p>Exposure to packages like NumPy, SciPy, Pandas, Matplotlib etc in Python or GGPlot2, dplyr, tidyR in R</p>\\n</li><li><p>Ability to communicate Model findings to both Technical and Non-Technical stake holders</p>\\n</li><li><p>Hands on experience in SQL/Hive or similar programming language</p>\\n</li><li><p>Must show past work via GitHub, Kaggle or any other published article</p>\\n</li><li><p>Master\'s degree in Statistics/Mathematics/Computer Science or any other quant specific field.</p></li></ul><di

In [10]:
from nltk.tokenize import sent_tokenize  # Sentence Tokenizer
from nltk.tokenize import word_tokenize  # Word Tokenizer

In [47]:
# Use BeautifulSoup to find all HTML tags in listings and decompose the tags
# see https://stackoverflow.com/questions/43736639/python-remove-html-tags-text-inbetween-html-tags
# Nope, nope, nope - didn't work

# Try search and split
html_tags = ['<div>', '</div>', '<ul>', '</ul>', '<li>', '</li>',
             '<p>', '</p>', '<b>', '</b>', '<h3>', '</h3>', '<br/>']
for tag in html_tags:
    if tag in job_listings:
        job_listings = ''.join(job_listings.split(tag))

In [46]:
type(job_listings)

str

In [48]:
job_listings

',description,title\n0,"b""Job Requirements:\\nConceptual understanding in Machine Learning models like Nai\\xc2\\xa8ve Bayes, K-Means, SVM, Apriori, Linear/ Logistic Regression, Neural, Random Forests, Decision Trees, K-NN along with hands-on experience in at least 2 of them\\nIntermediate to expert level coding skills in Python/R. (Ability to write functions, clean and efficient data manipulation are mandatory for this role)\\nExposure to packages like NumPy, SciPy, Pandas, Matplotlib etc in Python or GGPlot2, dplyr, tidyR in R\\nAbility to communicate Model findings to both Technical and Non-Technical stake holders\\nHands on experience in SQL/Hive or similar programming language\\nMust show past work via GitHub, Kaggle or any other published article\\nMaster\'s degree in Statistics/Mathematics/Computer Science or any other quant specific field.\\nApply Now""",Data scientist\xa0\n1,"b\'Job Description\\n\\nAs a Data Scientist 1, you will help us build machine learning models, data p

In [49]:
sentence_tokens = sent_tokenize(job_listings)
print(sentence_tokens)

[',description,title\n0,"b""Job Requirements:\\nConceptual understanding in Machine Learning models like Nai\\xc2\\xa8ve Bayes, K-Means, SVM, Apriori, Linear/ Logistic Regression, Neural, Random Forests, Decision Trees, K-NN along with hands-on experience in at least 2 of them\\nIntermediate to expert level coding skills in Python/R.', '(Ability to write functions, clean and efficient data manipulation are mandatory for this role)\\nExposure to packages like NumPy, SciPy, Pandas, Matplotlib etc in Python or GGPlot2, dplyr, tidyR in R\\nAbility to communicate Model findings to both Technical and Non-Technical stake holders\\nHands on experience in SQL/Hive or similar programming language\\nMust show past work via GitHub, Kaggle or any other published article\\nMaster\'s degree in Statistics/Mathematics/Computer Science or any other quant specific field.\\nApply Now""",Data scientist\xa0\n1,"b\'Job Description\\n\\nAs a Data Scientist 1, you will help us build machine learning models, da

In [55]:
sent_count = 0
tokens_list = []
for sent in sentence_tokens:
    sent_count += 1
    tokens = word_tokenize(sent)
    tokens_list.append(tokens)
print('\nThe sentence count is:', sent_count)


The sentence count is: 4153


# 3) Use Scikit-Learn's CountVectorizer to get word counts for each listing.

In [58]:
from sklearn.feature_extraction.text import CountVectorizer

# create the transform
vectorizer = CountVectorizer(lowercase=True, stop_words='english')

# tokenize and build vocab
for token in tokens_list:
    vectorizer.fit(token)

# Create a Vocabulary
# The vocabulary establishes all of the possible words that we might use.
print(vectorizer.vocabulary_)

# The vocabulary dictionary does not represent the counts of words!!

ValueError: empty vocabulary; perhaps the documents only contain stop words

# 4) Visualize the most common word counts

In [0]:
##### Your Code Here #####

 # 5) Use Scikit-Learn's tfidfVectorizer to get a TF-IDF feature matrix

In [0]:
##### Your Code Here #####

## Stretch Goals

 - Scrape Job Listings for the job title "Data Analyst". How do these differ from Data Scientist Job Listings
 - Try and identify requirements for experience specific technologies that are asked for in the job listings. How are those distributed among the job listings?
 - Use a clustering algorithm to cluster documents by their most important terms. Do the clusters reveal any common themes?
  - **Hint:** K-means might not be the best algorithm for this. Do a little bit of research to see what might be good for this. Also, remember that algorithms that depend on Euclidean distance break down with high dimensional data.